In [2]:
# 读取配置
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf,model_losss_juxiting

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()

signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )
    df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_yuanyou_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    # 数据处理
    df = datachuli(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)




从eta获取数据...
跳过指标 美国:东海岸地区:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 美国:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 美国:洛基山地区:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 美国:墨西哥湾沿岸:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 美国:西海岸地区:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 美国:中西部地区:炼油厂的投入与使用情况:开工率:四周均值
跳过指标 中国航班执行数/7DMA
跳过指标 美国汽油表需（周度）1周环差负值
跳过指标 美国汽油表需（周度）1周环差
跳过指标 美国汽油产量（周度）1周环差
跳过指标 美国原油周度表需/4WMA
跳过指标 美国油品表需/4WMA
跳过指标 美国油品表需4周环差
跳过指标 道琼斯旅游与休闲/标普500
跳过指标 DOE-柴油产量1周环差
跳过指标 DOE-美国汽油产量1周环差
跳过指标 美国航煤表需一周环差负值
跳过指标 美国馏分油表需一周环差负值
跳过指标 美国汽油表需一周环差负值
跳过指标 欧洲汽油裂差
跳过指标 欧洲柴油裂差
跳过指标 中国主营炼厂产能利用率1周环差
跳过指标 美国零售拥堵指数（周环比）/3WMA
跳过指标 美国炼厂原油输入量1周环差
跳过指标 美国炼厂原油输入量4周均值
跳过指标 美国柴油期货裂差
跳过指标 美国墨西哥湾柴油裂差
跳过指标 美国纽约港柴油裂差
跳过指标 欧洲柴油期货裂差
跳过指标 西北欧轻柴油裂差
跳过指标 新加坡柴油裂差
跳过指标 美国汽油期货裂差
跳过指标 美国墨西哥湾汽油裂差
跳过指标 美国纽约港汽油裂差
跳过指标 欧洲鹿特丹汽油裂差
跳过指标 新加坡汽油裂差


In [ ]:
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        row_dict['ds'] = row_dict['ds'].strftime('%Y-%m-%d %H:%M:%S')
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())




In [ ]:
import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 1
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    # 计算最近20天预测残差最低的模型名称

    model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
    # 删除空值率为40%以上的列
    print(model_results.shape)
    model_results = model_results.dropna(thresh=len(model_results)*0.6,axis=1)
    model_results = model_results.dropna()
    print(model_results.shape)
    modelnames  = model_results.columns.to_list()[2:] 
    for col in model_results[modelnames].select_dtypes(include=['object']).columns:
        model_results[col] = model_results[col].astype(np.float32)
    # 计算每个预测值与真实值之间的偏差率
    for model in modelnames:
        model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

    # 获取每行对应的最小偏差率值
    min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
    # 获取每行对应的最小偏差率值对应的列名
    min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
    print(min_abs_error_rate_column_name)
    # 将列名索引转换为列名
    min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # 取出现次数最多的模型名称
    most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
    logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))



In [ ]:
if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape


In [ ]:
now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')
ex_Model(df,
        horizon=horizon,
        input_size=input_size,
        train_steps=train_steps,
        val_check_steps=val_check_steps,
        early_stop_patience_steps=early_stop_patience_steps,
        is_debug=is_debug,
        dataset=dataset,
        is_train=is_train,
        is_fivemodels=is_fivemodels,
        val_size=val_size,
        test_size=test_size,
        settings=settings,
        now=now,
        etadata = etadata,
        modelsindex = modelsindex,
        data = data,
        is_eta=is_eta,
        )


In [ ]:
logger.info('模型训练完成')
# # 模型评估

pd.set_option('display.max_columns', 100)
# 计算预测评估指数
def model_losss_juxiting(sqlitedb):
    global dataset
    # 数据库查询最佳模型名称
    most_model = [sqlitedb.select_data('most_model',columns=['most_common_model'],order_by='ds desc',limit=1).values[0][0]]
    most_model_name = most_model[0]

    # 预测数据处理 predict
    df_combined = loadcsv(os.path.join(dataset,"cross_validation.csv"))  
    df_combined = dateConvert(df_combined)
    # 删除空列
    df_combined.dropna(axis=1,inplace=True)
     # 删除缺失值,预测过程不能有缺失值
    df_combined.dropna(inplace=True) 
    # 其他列转为数值类型
    df_combined = df_combined.astype({col: 'float32' for col in df_combined.columns if col not in ['cutoff','ds'] })
    # 使用 groupby 和 transform 结合 lambda 函数来获取每个分组中 cutoff 的最小值，并创建一个新的列来存储这个最大值
    df_combined['max_cutoff'] = df_combined.groupby('ds')['cutoff'].transform('max')

    # 然后筛选出那些 cutoff 等于 max_cutoff 的行，这样就得到了每个分组中 cutoff 最大的行，并保留了其他列
    df_combined = df_combined[df_combined['cutoff'] == df_combined['max_cutoff']]
    # 删除模型生成的cutoff列
    df_combined.drop(columns=['cutoff', 'max_cutoff'], inplace=True)
    # 获取模型名称
    modelnames  = df_combined.columns.to_list()[1:] 
    if 'y' in modelnames:
        modelnames.remove('y')
    df_combined3 = df_combined.copy()  # 备份df_combined,后面画图需要


    # 空的列表存储每个模型的MSE、RMSE、MAE、MAPE、SMAPE
    cellText = []

    # 遍历模型名称，计算模型评估指标  
    for model in modelnames:
        modelmse = mse(df_combined['y'], df_combined[model])
        modelrmse = rmse(df_combined['y'], df_combined[model])
        modelmae = mae(df_combined['y'], df_combined[model])
        # modelmape = mape(df_combined['y'], df_combined[model])
        # modelsmape = smape(df_combined['y'], df_combined[model])
        # modelr2 = r2_score(df_combined['y'], df_combined[model])
        cellText.append([model,round(modelmse, 3), round(modelrmse, 3), round(modelmae, 3)])
        
    model_results3 = pd.DataFrame(cellText,columns=['模型(Model)','平均平方误差(MSE)', '均方根误差(RMSE)',  '平均绝对误差(MAE)'])
    # 按MSE降序排列
    model_results3 = model_results3.sort_values(by='平均平方误差(MSE)', ascending=True)
    model_results3.to_csv(os.path.join(dataset,"model_evaluation.csv"),index=False)
    modelnames = model_results3['模型(Model)'].tolist()
    allmodelnames = modelnames.copy()
    # 保存5个最佳模型的名称
    if len(modelnames) > 5:
        modelnames = modelnames[0:5]
    with open(os.path.join(dataset,"best_modelnames.txt"), 'w') as f:
        f.write(','.join(modelnames) + '\n')


    # 去掉方差最大的模型，其余模型预测最大最小值确定通道边界
    best_models = pd.read_csv(os.path.join(dataset,'best_modelnames.txt'),header=None).values.flatten().tolist()
   

    # 预测值与真实值对比图
    plt.rcParams['font.sans-serif'] = ['SimHei']
    plt.figure(figsize=(15, 10))
    # 设置有5个子图的画布
    for n,model in enumerate(modelnames[:5]):
        plt.subplot(3, 2, n+1)
        plt.plot(df_combined3['ds'], df_combined3['y'], label='真实值')
        plt.plot(df_combined3['ds'], df_combined3[model], label=model)
        plt.legend()
        plt.xlabel('日期')
        plt.ylabel('价格')
        plt.title(model+'拟合')
    plt.subplots_adjust(hspace=0.5)
    plt.savefig(os.path.join(dataset,'预测值与真实值对比图.png'), bbox_inches='tight')
    plt.close()
    
    # 历史数据+预测数据
    # 拼接未来时间预测
    df_predict  = loadcsv(os.path.join(dataset,'predict.csv'))
    df_predict.drop('unique_id',inplace=True,axis=1)
    df_predict.dropna(axis=1,inplace=True)
    df_predict2 = df_predict.copy()
    try:
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y-%m-%d')
    except ValueError :
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y/%m/%d')

    # 取第一行数据存储到数据库中
    first_row = df_predict.head(1)
    first_row['ds'] = first_row['ds'].dt.strftime('%Y-%m-%d 00:00:00')

    # # 将预测结果保存到数据库
    # # 判断表存在
    if not sqlitedb.check_table_exists('testandpredict_groupby'):
        df_predict2.to_sql('testandpredict_groupby',sqlitedb.connection,index=False)
    else:
        for row in df_predict2.itertuples(index=False):
            row_dict = row._asdict()
            check_query = sqlitedb.select_data('testandpredict_groupby',where_condition = f"ds = '{row.ds}'")
            if len(check_query) > 0:
                set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
                sqlitedb.update_data('testandpredict_groupby',set_clause,where_condition = f"ds = '{row.ds}'")
                continue
            sqlitedb.insert_data('testandpredict_groupby',tuple(row_dict.values()),columns=row_dict.keys())

    df_combined3 = pd.concat([df_combined3, df_predict]).reset_index(drop=True)

    # # 判断 df 的数值列转为float
    for col in df_combined3.columns:
        try:
            if col != 'ds':
                df_combined3[col] = df_combined3[col].astype(float)
                df_combined3[col] = df_combined3[col].round(2)
        except ValueError:
            pass
    df_combined3.to_csv(os.path.join(dataset,"df_combined3.csv"),index=False) 
    df_combined3.to_sql('testandpredict_groupby', sqlitedb.connection, if_exists='replace', index=False)
    df_combined3.to_csv(os.path.join(dataset,"testandpredict_groupby.csv"),index=False)
    
    
    ten_models = allmodelnames
    # 计算每个模型的方差
    variances = df_combined3[ten_models].var()
    # 找到方差最大的模型
    max_variance_model = variances.idxmax()
    # 打印方差最大的模型
    print("方差最大的模型是：", max_variance_model)
    # 去掉方差最大的模型
    df_combined3 = df_combined3.drop(columns=[max_variance_model])
    if max_variance_model in allmodelnames:
        allmodelnames.remove(max_variance_model)
    df_combined3['min'] = df_combined3[allmodelnames].min(axis=1)
    df_combined3['max'] = df_combined3[allmodelnames].max(axis=1)
    print(df_combined3[['min','max']])
    # 历史价格+预测价格
    df_combined3 = df_combined3[-50:] # 取50个数据点画图
    plt.figure(figsize=(20, 10))
    plt.plot(df_combined3['ds'], df_combined3['y'], label='真实值',marker='o')
    plt.plot(df_combined3['ds'], df_combined3[most_model], label=most_model_name)
    plt.fill_between(df_combined3['ds'], df_combined3['min'], df_combined3['max'], alpha=0.2)
    plt.grid(True)
    # 当前日期画竖虚线
    plt.axvline(x=df_combined3['ds'].iloc[-horizon], color='r', linestyle='--')
    plt.legend()
    plt.xlabel('日期')
    plt.ylabel('价格')

    # # 显示历史值
    for i, j in zip(df_combined3['ds'][:-5], df_combined3['y'][:-5]):
        plt.text(i, j, str(j), ha='center', va='bottom')
    plt.savefig(os.path.join(dataset,'历史价格-预测值.png'), bbox_inches='tight')
    plt.show()
    plt.close()
       
    # 预测值表格
    fig, ax = plt.subplots(figsize=(20, 6))
    ax.axis('off')  # 关闭坐标轴
    # 数值保留2位小数
    df_combined3 = df_combined3.round(2)
    df_combined3 = df_combined3[-horizon:]
    df_combined3['Day'] = [f'Day_{i}' for i in range(1,horizon+1)]
    # Day列放到最前面
    df_combined3 = df_combined3[['Day'] + list(df_combined3.columns[:-1])]
    table = ax.table(cellText=df_combined3.values, colLabels=df_combined3.columns, loc='center')
    #加宽表格
    table.auto_set_font_size(False)
    table.set_fontsize(10)

    # 设置表格样式，列数据最小的用绿色标识
    plt.savefig(os.path.join(dataset,'预测值表格.png'), bbox_inches='tight')
    plt.close()
    # plt.show()
       
    # 可视化评估结果
    plt.rcParams['font.sans-serif'] = ['SimHei']
    fig, ax = plt.subplots(figsize=(20, 10))
    ax.axis('off')  # 关闭坐标轴
    table = ax.table(cellText=model_results3.values, colLabels=model_results3.columns, loc='center')
    # 加宽表格
    table.auto_set_font_size(False)
    table.set_fontsize(10)

    # 设置表格样式，列数据最小的用绿色标识
    plt.savefig(os.path.join(dataset,'模型评估.png'), bbox_inches='tight')
    plt.close()
    return model_results3




logger.info('训练数据绘图ing')
model_results3 = model_losss_juxiting(sqlitedb)

logger.info('训练数据绘图end')



In [ ]:
# 模型报告

logger.info('制作报告ing')
title = f'{settings}--{now}-预测报告' # 报告标题

pp_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
        reportname=reportname,sqlitedb=sqlitedb),

logger.info('制作报告end')
logger.info('模型训练完成')

In [ ]:
# 发送邮件
m = SendMail(
    username=username,
    passwd=passwd,
    recv=recv,
    title=title,
    content=content,
    file=max(glob.glob(os.path.join(dataset,'*.pdf')), key=os.path.getctime),
    ssl=ssl,
)
# m.send_mail()   
